In [11]:
from gensim.models import KeyedVectors, FastText, fasttext
import nltk
from tqdm.notebook import tqdm
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
import gensim.downloader as api


Можно использовать эту модель, но памяти может не хватить (может съесть до 20 гб)

In [ ]:
# !wget https://dl.fbaipublicfiles.com/fasttext/vectors-english/crawl-300d-2M-subword.zip
# !unzip -d fasttext-en-crawl crawl-300d-2M-subword.zip
# model = fasttext.load_facebook_model("fasttext-en-crawl/crawl-300d-2M-subword.bin")

In [ ]:
# !wget https://dl.fbaipublicfiles.com/fasttext/vectors-english/crawl-300d-2M.vec.zip

In [6]:
!wget -c "https://s3.amazonaws.com/dl4j-distribution/GoogleNews-vectors-negative300.bin.gz"

--2020-02-24 19:58:41--  https://s3.amazonaws.com/dl4j-distribution/GoogleNews-vectors-negative300.bin.gz
Resolving s3.amazonaws.com (s3.amazonaws.com)... 52.216.114.93
Connecting to s3.amazonaws.com (s3.amazonaws.com)|52.216.114.93|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1647046227 (1.5G) [application/x-gzip]
Saving to: ‘GoogleNews-vectors-negative300.bin.gz’

GoogleNews-vectors- 100%[===================>]   1.53G  30.9MB/s    in 94s     

2020-02-24 20:00:15 (16.8 MB/s) - ‘GoogleNews-vectors-negative300.bin.gz’ saved [1647046227/1647046227]



Грузится долго, но быстрее большинства (размер гигов 5-8)

In [7]:
model = KeyedVectors.load_word2vec_format("GoogleNews-vectors-negative300.bin.gz", binary=True)

In [8]:
model.most_similar("can't")

[("don't", 0.5761473774909973),
 ("let's", 0.570459246635437),
 ("I'll", 0.5250788331031799),
 ("couldn't", 0.5167351961135864),
 ("it's", 0.5124365091323853),
 ("I'm_gonna", 0.504035234451294),
 ("doesn't", 0.4948706030845642),
 ("you've_got", 0.4888979494571686),
 ('gotta', 0.47242504358291626),
 ("didn't", 0.46968358755111694)]

In [33]:
model.most_similar("cat")

[('cats', 0.8099379539489746),
 ('dog', 0.7609456777572632),
 ('kitten', 0.7464985251426697),
 ('feline', 0.7326233983039856),
 ('beagle', 0.7150583267211914),
 ('puppy', 0.7075453996658325),
 ('pup', 0.6934291124343872),
 ('pet', 0.6891531348228455),
 ('felines', 0.6755931377410889),
 ('chihuahua', 0.6709762215614319)]

In [49]:
model.most_similar(["russia", "london"], ["moscow"])

[('england', 0.5279598236083984),
 ('asia', 0.5255308151245117),
 ('europe', 0.5157119631767273),
 ('washington', 0.49427759647369385),
 ('africa', 0.49311724305152893),
 ('korea', 0.4915522336959839),
 ('pakistan', 0.4880489408969879),
 ('america', 0.4868756830692291),
 ('sweden', 0.4815259277820587),
 ('tennessee', 0.47477439045906067)]

In [12]:
tokenizer = nltk.tokenize.TweetTokenizer()

Превращаем тексты, разбитые на слова, в векторы. В модели уже натренирован вектор для каждого известного ей слова. Остается их достать и сложить. Для этого разобьем тексты на токены (слова по большей части). Для каждого текста возьмём векторы токенов, известные модели (model.vocab), соединим их в матрицу и просуммируем её строки. 

Альтернативные параметры:
- word_set - множество слов, которые можно использовать. Если None - можно использовать все. Например, можно отсеять все слишком частые или слишком редкие слова. 
- normalize - привести ли векторы к единичной норме. Часто это помогает. Не стоит забывать, что основная метрика сходства - косинус, который игнорирует норму.
- word_weights  словарь вида {слово:вес}. Если такой задан (для каждого слова в word_set, который обязателен при его использовании), сумма будет взвешена.
- average - поделить ли сумму на число слагаемых

In [13]:
def tokenized_to_cbow(model, tokenized_texts, word_set=None, word_weights=None, normalize=False, average=False):
    result = []
    assert bool(word_set) == bool(word_weights)
    for tokens in tqdm(tokenized_texts):
        if word_set:
            tokens = [t for t in tokens if t in word_set]

        # word in model.vocab - это условие можно убрать для fasttext моделей, у которых есть обработка подслов
        word_vectors = np.array([model[word] for word in tokens if word in model.vocab])
        if word_weights:
            token_weights = np.array([word_weights[w] for w in tokens if w in model.vocab])
            text_vector = np.dot(token_weights, word_vectors)
        else:
            text_vector = word_vectors.sum(axis=0)
        if normalize:
            norm = np.linalg.norm(text_vector)
            if norm > 0.0000001:
                text_vector /= np.linalg.norm(text_vector)
        elif average:
            text_vector /= len(tokens)
        result.append(text_vector)
    return np.array(result)

In [14]:
sample_text = "Hi, it's me"
sample_tokens = tokenizer.tokenize(sample_text)
print(sample_tokens)

['Hi', ',', "it's", 'me']


In [15]:
np.random.seed(65001)
imdb_df = pd.read_csv('imdb_master.csv', encoding='latin-1')
imdb_supervised = imdb_df[imdb_df['label'].isin(['pos','neg'])]
imdb_train_dev = imdb_supervised[imdb_supervised['type'] == 'train']
imdb_test = imdb_supervised[imdb_supervised['type'] == 'test']
imdb_train, imdb_dev = train_test_split(imdb_train_dev, test_size=0.2)

In [16]:
imdb_train.sample(5)

number   type                                             review label  \
47836   47836  train  This is of of Sammo's great early comedy films...   pos   
45521   45521  train  I love this movie and never get tired of watch...   pos   
43397   43397  train  Retitled from its original Japanese name of LA...   pos   
28878   28878  train  The "saucy" misadventures of four au pairs who...   neg   
35102   35102  train  This is a weak sequel: it lacks the interest a...   neg   

              file  
47836   8053_8.txt  
45521  5970_10.txt  
43397  4058_10.txt  
28878   2240_4.txt  
35102   7843_4.txt

In [17]:
labels_mapping = {"neg": 0, "pos": 1}
labels_train = np.array([labels_mapping[lbl] for lbl in imdb_train.label])
labels_dev = np.array([labels_mapping[lbl] for lbl in imdb_dev.label])

In [18]:
def tokenize_texts(texts):
    tokenizer = nltk.tokenize.TweetTokenizer(preserve_case=False)
    result = []
    for text in tqdm(texts):
        result.append(tokenizer.tokenize(text))
    return result

In [19]:
tokens_train, tokens_dev = [tokenize_texts(df.review) for df in [imdb_train, imdb_dev]]

In [21]:
tokens_train

[['this',
  'documentary',
  'was',
  'nominated',
  'for',
  'an',
  'oscar',
  'and',
  "it's",
  'easy',
  'to',
  'see',
  'why',
  '.',
  'even',
  '45',
  'years',
  'later',
  ',',
  'it',
  'is',
  'quite',
  'an',
  'impressive',
  'piece',
  'of',
  'work',
  '.',
  'why',
  'it',
  "isn't",
  'in-print',
  'is',
  'a',
  'mystery',
  'that',
  'only',
  'disney',
  'can',
  'explain',
  '.',
  'good',
  'use',
  'of',
  'live',
  'footage',
  'and',
  'animation',
  'in',
  'tandem',
  '.',
  'this',
  'used',
  'to',
  'run',
  'as',
  'part',
  'of',
  '"',
  'vault',
  'disney',
  '"',
  'every',
  'few',
  'months',
  'or',
  'so',
  ',',
  'but',
  'i',
  "haven't",
  'seen',
  'it',
  'listed',
  'in',
  'quite',
  'a',
  'while',
  '.',
  '*',
  'sigh',
  '*',
  'most',
  'recommended',
  '.'],
 ['i',
  'would',
  'like',
  'to',
  'say',
  'that',
  'curiosity',
  'got',
  'the',
  'best',
  'of',
  'me',
  '.',
  'if',
  'only',
  'i',
  'saw',
  'a',
  'trailer',
 

In [20]:
cbow_train = tokenized_to_cbow(model, tokens_train)

NameError: name 'model' is not defined

In [ ]:
cbow_dev = tokenized_to_cbow(model,tokens_dev)

In [43]:
print(cbow_dev.shape)

(5000, 300)


In [44]:
logr = LogisticRegression(max_iter=2000).fit(cbow_train, labels_train)

In [45]:
logr.score(cbow_dev, labels_dev)

0.8626

In [1]:
cbow_train

NameError: name 'cbow_train' is not defined